In [5]:
import os
import cv2
import torch
import numpy as np
from PIL import Image
from ultralytics import YOLO  # Assuming YOLOv8 is being used
from sam2.build_sam import build_sam2_video_predictor
from torch.utils.checkpoint import checkpoint
from torch.utils.data import DataLoader, Dataset
from torch.cuda.amp import autocast, GradScaler

# Paths and Directories
video_path = './clip 2.mp4'
output_frames_dir = './video_frames'
output_video_path = 'segmented_video.mp4'

# Create directory to store frames
os.makedirs(output_frames_dir, exist_ok=True)

# Load Video and Extract Frames
cap = cv2.VideoCapture(video_path)
frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
fps = int(cap.get(cv2.CAP_PROP_FPS))

frame_names = []
for i in range(frame_count):
    ret, frame = cap.read()
    if not ret:
        break
    frame_name = f'{i:05d}.jpg'
    cv2.imwrite(os.path.join(output_frames_dir, frame_name), frame)
    frame_names.append(frame_name)
cap.release()


# Custom Dataset for Batch Processing
class VideoFrameDataset(torch.utils.data.Dataset):
    def __init__(self, frame_names, frame_dir,target_size=(640, 640)):
        self.frame_names = frame_names
        self.frame_dir = frame_dir
        self.target_size = target_size  # (Height, Width)
    def __len__(self):
        return len(self.frame_names)

    def __getitem__(self, idx):
        frame_path = os.path.join(self.frame_dir, self.frame_names[idx])
        frame = Image.open(frame_path).convert('RGB')
        frame = frame.resize(self.target_size, Image.BILINEAR)
        frame_np = np.array(frame)
        # Convert to (C, H, W)
        frame_np = frame_np.transpose(2, 0, 1)
        frame_tensor = torch.from_numpy(frame_np).float() / 255.0  # Normalize to [0,1]
        return frame_tensor, idx

# Load Dataset
dataset = VideoFrameDataset(frame_names, output_frames_dir)
batch_size = 8 # Adjust batch size based on GPU memory
dataloader = torch.utils.data.DataLoader(dataset, batch_size=batch_size, shuffle=False)

# Load SAM 2 Model
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
sam2_checkpoint = "./segment-anything-2/checkpoints/sam2_hiera_small.pt"
model_cfg = "sam2_hiera_s.yaml"
predictor = build_sam2_video_predictor(model_cfg, sam2_checkpoint, device=device)

# Initialize YOLO model for object detection
yolo_model = YOLO('yolov8s.pt').to(device)  # Use the best YOLO model variant

# Initialize SAM 2 State
inference_state = predictor.init_state(video_path=output_frames_dir)
predictor.reset_state(inference_state)

ann_obj_id = 1  # Initialize object ID



    
# Process frames in batches
video_segments = {}
for batch_frames, batch_indices in dataloader:
    batch_frames = batch_frames.to(device)

    # YOLO Object Detection with Gradient Checkpointing
    with autocast():
        results = yolo_model(batch_frames, imgsz=640)  # Ensure img size matches target_size

    for i, frame_idx in enumerate(batch_indices):
        detected_boxes = results[i].boxes.xyxy.cpu().numpy().astype(np.float32)  # Shape: (num_boxes, 4)

        # Add detected boxes to SAM 2 for segmentation
        for single_box in detected_boxes:
            # SAM expects boxes in [x1, y1, x2, y2] format
            _, out_obj_ids, out_mask_logits = predictor.add_new_points_or_box(
                inference_state=inference_state,
                frame_idx=int(frame_idx),
                obj_id=ann_obj_id,
                box=single_box.tolist(),  # Convert to list if necessary
            )
            ann_obj_id += 1

        # Propagate masks in video after adding new objects
        video_segments[int(frame_idx)] = {
            out_obj_id: (out_mask_logits[i] > 0.0).cpu().numpy()
            for i, out_obj_id in enumerate(out_obj_ids)
        }
          # Clear cache to free up memory
    torch.cuda.empty_cache()

# Save the Segmented Video
# Assuming all frames are resized to target_size
height, width = dataset.target_size
fourcc = cv2.VideoWriter_fourcc(*'mp4v')

out = cv2.VideoWriter(output_video_path, fourcc, fps, (width, height))

for out_frame_idx in range(frame_count):
    # Load the resized frame
    frame_path = os.path.join(output_frames_dir, frame_names[out_frame_idx])
    frame = cv2.imread(frame_path)
    frame = cv2.resize(frame, (width, height))  # Ensure size matches target_size

    if out_frame_idx in video_segments:
        for out_obj_id, out_mask in video_segments[out_frame_idx].items():
            # Create a color overlay for the mask
            color = np.array([0, 255, 0], dtype=np.uint8)  # Green mask
            mask = (out_mask * 255).astype(np.uint8)
            mask_rgb = cv2.merge([mask, mask, mask])
            colored_mask = cv2.bitwise_and(color, color, mask=mask)
            # Blend the mask with the frame
            frame = cv2.addWeighted(frame, 1.0, colored_mask, 0.5, 0)
    out.write(frame)

out.release()

print(f'Segmented video saved to {output_video_path}')


100%|██████████| 21.5M/21.5M [00:00<00:00, 32.3MB/s]
frame loading (JPEG): 100%|██████████| 2395/2395 [02:09<00:00, 18.46it/s]


OutOfMemoryError: CUDA out of memory. Tried to allocate 28.07 GiB. GPU 0 has a total capacity of 8.00 GiB of which 0 bytes is free. Of the allocated memory 29.46 GiB is allocated by PyTorch, and 198.65 MiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)

In [1]:
import os
import cv2
import torch
import numpy as np
from PIL import Image
from ultralytics import YOLO  # Ensure you have ultralytics installed
from sam2.build_sam import build_sam2_video_predictor
from torch.utils.checkpoint import checkpoint
from torch.cuda.amp import autocast, GradScaler
from torch.utils.data import DataLoader, Dataset
from tqdm import tqdm  # For progress bars

# Paths and Directories
video_path = './clip 1.mp4'
output_frames_dir = './video_frames'
output_video_path = 'segmented_video.mp4'

# Create directory to store frames
os.makedirs(output_frames_dir, exist_ok=True)

# Load Video and Extract Frames
def extract_frames(video_path, output_dir):
    cap = cv2.VideoCapture(video_path)
    frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    fps = cap.get(cv2.CAP_PROP_FPS)
    
    frame_names = []
    for i in tqdm(range(frame_count), desc="Extracting frames"):
        ret, frame = cap.read()
        if not ret:
            break
        frame_name = f'{i:05d}.jpg'
        cv2.imwrite(os.path.join(output_frames_dir, frame_name), frame)
        frame_names.append(frame_name)
    cap.release()
    return frame_names, fps

frame_names, fps = extract_frames(video_path, output_frames_dir)

# Custom Dataset for Batch Processing
class VideoFrameDataset(Dataset):
    def __init__(self, frame_names, frame_dir, target_size=(320, 320)):
        self.frame_names = frame_names
        self.frame_dir = frame_dir
        self.target_size = target_size  # (Width, Height)
    
    def __len__(self):
        return len(self.frame_names)
    
    def __getitem__(self, idx):
        frame_path = os.path.join(self.frame_dir, self.frame_names[idx])
        frame = Image.open(frame_path).convert('RGB')
        frame = frame.resize(self.target_size, Image.BILINEAR)
        frame_np = np.array(frame)
        # Convert to (C, H, W)
        frame_np = frame_np.transpose(2, 0, 1)
        frame_tensor = torch.from_numpy(frame_np).float() / 255.0  # Normalize to [0,1]
        return frame_tensor, idx

# Load Dataset and DataLoader
dataset = VideoFrameDataset(frame_names, output_frames_dir)
batch_size = 1  # Reduced batch size to minimize memory usage
dataloader = torch.utils.data.DataLoader(dataset, batch_size=batch_size, shuffle=False, num_workers=0)
# Check for CUDA and set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Load SAM 2 Model and move it to GPU if available
sam2_checkpoint = "./segment-anything-2/checkpoints/sam2_hiera_small.pt"  # Ensure this path is correct
model_cfg = "sam2_hiera_s.yaml"  # Ensure this config file is present
try:
    predictor = build_sam2_video_predictor(model_cfg, sam2_checkpoint, device=device)
except RuntimeError as e:
    print(f"Error loading SAM 2 model: {e}")
    exit()

# Initialize YOLO model for object detection and move to GPU if available
yolo_model = YOLO('yolov8s.pt').to(device)  # Using a smaller YOLO model variant

# Initialize SAM 2 State with offloading frames to CPU to save GPU memory
inference_state = predictor.init_state(
    video_path=output_frames_dir,
    offload_video_to_cpu=True  # Offload video frames to CPU
)
predictor.reset_state(inference_state)

ann_obj_id = 1  # Initialize object ID

# Dictionary to store segmentation masks
video_segments = {}

# Process frames in batches
scaler = GradScaler()  # For mixed precision training
for batch_frames, batch_indices in tqdm(dataloader, desc="Processing batches"):
    batch_frames = batch_frames.to(device, non_blocking=True)
    
    with torch.no_grad():  # Disable gradient calculations for inference
        with autocast():  # Enable mixed precision
            # Perform YOLO object detection on the batch
            results = yolo_model(batch_frames, imgsz=320)  # Ensure img size matches target_size
    
    for i, frame_idx in enumerate(batch_indices):
        detected_boxes = results[i].boxes.xyxy.cpu().numpy().astype(np.float32)  # Shape: (num_boxes, 4)
        
        # Add detected boxes to SAM 2 for segmentation
        for single_box in detected_boxes:
            # SAM expects boxes in [x1, y1, x2, y2] format
            try:
                _, out_obj_ids, out_mask_logits = predictor.add_new_points_or_box(
                    inference_state=inference_state,
                    frame_idx=int(frame_idx),
                    obj_id=ann_obj_id,
                    box=single_box.tolist(),  # Convert to list if necessary
                )
                ann_obj_id += 1
            except Exception as e:
                print(f"Error processing frame {frame_idx} with box {single_box}: {e}")
                continue
    
        # Propagate masks in video after adding new objects
        try:
            video_segments[int(frame_idx)] = {
                out_obj_id: (out_mask_logits[i] > 0.0).cpu().numpy()
                for i, out_obj_id in enumerate(out_obj_ids)
            }
        except Exception as e:
            print(f"Error propagating masks for frame {frame_idx}: {e}")
            continue
    
    # Clear cache to free up memory
    torch.cuda.empty_cache()

# Save the Segmented Video
def save_segmented_video(output_path, frame_names, video_segments, target_size=(320, 320)):
    height, width = target_size
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = cv2.VideoWriter(output_path, fourcc, fps, (width, height))
    
    for idx in tqdm(range(len(frame_names)), desc="Saving video"):
        frame_path = os.path.join(output_frames_dir, frame_names[idx])
        frame = cv2.imread(frame_path)
        if frame is None:
            print(f"Warning: Unable to read frame at {frame_path}. Skipping.")
            continue
        frame = cv2.resize(frame, (width, height))  # Ensure size matches target_size

        if idx in video_segments:
            for out_obj_id, out_mask in video_segments[idx].items():
                # Squeeze the mask to remove any single-dimensional entries
                out_mask = np.squeeze(out_mask)

                # Debug: Print the mask shape after squeezing
                print(f"Debug: Mask shape after squeezing: {out_mask.shape}")

                # Convert mask to uint8 and ensure it's single-channel
                mask = (out_mask * 255).astype(np.uint8)
                
                # Check if resizing parameters are valid and the mask is non-empty
                if mask.shape[0] > 0 and mask.shape[1] > 0 and width > 0 and height > 0:
                    mask = cv2.resize(mask, (width, height))  # Resize mask to match frame size
                else:
                    print(f"Error: Invalid mask size or target size for resizing mask in frame {idx}. Skipping.")
                    continue

                # Define the color for the mask (Green in this case)
                color = np.array([0, 255, 0], dtype=np.uint8)  # BGR format for OpenCV

                # Create a 3-channel colored mask
                colored_mask = np.zeros_like(frame, dtype=np.uint8)
                colored_mask[:, :] = color  # Fill with the specified color

                # Apply the mask to the colored mask image
                colored_mask = cv2.bitwise_and(colored_mask, colored_mask, mask=mask)

                # Blend the colored mask with the original frame
                frame = cv2.addWeighted(frame, 1.0, colored_mask, 0.5, 0)
        
        out.write(frame)
    
    out.release()
    print(f'Segmented video saved to {output_path}')

save_segmented_video(output_video_path, frame_names, video_segments, target_size=(320, 320))


Extracting frames: 100%|██████████| 153/153 [00:06<00:00, 22.35it/s]


Using device: cuda


frame loading (JPEG): 100%|██████████| 476/476 [00:37<00:00, 12.85it/s]
C:\Users\varun\anaconda3\envs\sam2\Lib\site-packages\sam_2-1.0-py3.12-win-amd64.egg\sam2\modeling\backbones\hieradet.py:68: UserWarning: 1Torch was not compiled with flash attention. (Triggered internally at C:\cb\pytorch_1000000000000\work\aten\src\ATen\native\transformers\cuda\sdp_utils.cpp:555.)
  x = F.scaled_dot_product_attention(
Processing batches:   0%|          | 0/153 [00:00<?, ?it/s]


0: 320x320 2 cars, 15.0ms
Speed: 0.0ms preprocess, 15.0ms inference, 68.9ms postprocess per image at shape (1, 3, 320, 320)


C:\Users\varun\anaconda3\envs\sam2\Lib\site-packages\sam_2-1.0-py3.12-win-amd64.egg\sam2\modeling\sam\transformer.py:270: UserWarning: Memory efficient kernel not used because: (Triggered internally at C:\cb\pytorch_1000000000000\work\aten\src\ATen\native\transformers\cuda\sdp_utils.cpp:718.)
  out = F.scaled_dot_product_attention(q, k, v, dropout_p=dropout_p)
C:\Users\varun\anaconda3\envs\sam2\Lib\site-packages\sam_2-1.0-py3.12-win-amd64.egg\sam2\modeling\sam\transformer.py:270: UserWarning: Memory Efficient attention has been runtime disabled. (Triggered internally at C:\cb\pytorch_1000000000000\work\aten\src\ATen/native/transformers/sdp_utils_cpp.h:495.)
  out = F.scaled_dot_product_attention(q, k, v, dropout_p=dropout_p)
C:\Users\varun\anaconda3\envs\sam2\Lib\site-packages\sam_2-1.0-py3.12-win-amd64.egg\sam2\modeling\sam\transformer.py:270: UserWarning: Flash attention kernel not used because: (Triggered internally at C:\cb\pytorch_1000000000000\work\aten\src\ATen\native\transforme

...

Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080

Saving video:  99%|█████████▉| 152/153 [06:21<00:04,  4.44s/it]

Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080

Saving video: 100%|██████████| 153/153 [06:25<00:00,  2.52s/it]

Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Debug: Mask shape after squeezing: (1080, 2520)
Segmented video saved to segmented_video.mp4


In [3]:
import os
import cv2
import torch
import numpy as np
from PIL import Image
from ultralytics import YOLO  # Ensure you have ultralytics installed
from sam2.build_sam import build_sam2_video_predictor
from torch.utils.checkpoint import checkpoint
from torch.cuda.amp import autocast, GradScaler
from torch.utils.data import DataLoader, Dataset
from tqdm import tqdm  # For progress bars

# Paths and Directories
video_path = './clip 1.mp4'
output_frames_dir = './video_frames'
output_video_path = 'segmented_video.mp4'

# Create directory to store frames
os.makedirs(output_frames_dir, exist_ok=True)

# Load Video and Extract Frames
def extract_frames(video_path, output_dir):
    cap = cv2.VideoCapture(video_path)
    frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    fps = cap.get(cv2.CAP_PROP_FPS)
    
    frame_names = []
    for i in tqdm(range(frame_count), desc="Extracting frames"):
        ret, frame = cap.read()
        if not ret:
            break
        frame_name = f'{i:05d}.jpg'
        cv2.imwrite(os.path.join(output_frames_dir, frame_name), frame)
        frame_names.append(frame_name)
    cap.release()
    return frame_names, fps

frame_names, fps = extract_frames(video_path, output_frames_dir)

# Custom Dataset for Batch Processing
class VideoFrameDataset(Dataset):
    def __init__(self, frame_names, frame_dir, target_size=(320, 320)):
        self.frame_names = frame_names
        self.frame_dir = frame_dir
        self.target_size = target_size  # (Width, Height)
    
    def __len__(self):
        return len(self.frame_names)
    
    def __getitem__(self, idx):
        frame_path = os.path.join(self.frame_dir, self.frame_names[idx])
        frame = Image.open(frame_path).convert('RGB')
        frame = frame.resize(self.target_size, Image.BILINEAR)
        frame_np = np.array(frame)
        # Convert to (C, H, W)
        frame_np = frame_np.transpose(2, 0, 1)
        frame_tensor = torch.from_numpy(frame_np).float() / 255.0  # Normalize to [0,1]
        return frame_tensor, idx

# Load Dataset and DataLoader
dataset = VideoFrameDataset(frame_names, output_frames_dir)
batch_size = 1  # Reduced batch size to minimize memory usage
dataloader = torch.utils.data.DataLoader(dataset, batch_size=batch_size, shuffle=False, num_workers=0)
# Check for CUDA and set device
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

# Load SAM 2 Model and move it to GPU if available
sam2_checkpoint = "./segment-anything-2/checkpoints/sam2_hiera_small.pt"  # Ensure this path is correct
model_cfg = "sam2_hiera_s.yaml"  # Ensure this config file is present
try:
    predictor = build_sam2_video_predictor(model_cfg, sam2_checkpoint, device=device)
except RuntimeError as e:
    print(f"Error loading SAM 2 model: {e}")
    exit()

# Initialize YOLO model for object detection and move to GPU if available
yolo_model = YOLO('yolov8s.pt').to(device)  # Using a smaller YOLO model variant

# Initialize SAM 2 State with offloading frames to CPU to save GPU memory
inference_state = predictor.init_state(
    video_path=output_frames_dir,
    offload_video_to_cpu=True  # Offload video frames to CPU
)
predictor.reset_state(inference_state)

ann_obj_id = 1  # Initialize object ID

# Dictionary to store segmentation masks
video_segments = {}

# Process frames in batches
scaler = GradScaler()  # For mixed precision training
for batch_frames, batch_indices in tqdm(dataloader, desc="Processing batches"):
    batch_frames = batch_frames.to(device, non_blocking=True)
    
    with torch.no_grad():  # Disable gradient calculations for inference
        with autocast():  # Enable mixed precision
            # Perform YOLO object detection on the batch
            results = yolo_model(batch_frames, imgsz=320)  # Ensure img size matches target_size
    
    for i, frame_idx in enumerate(batch_indices):
        detected_boxes = results[i].boxes.xyxy.cpu().numpy().astype(np.float32)  # Shape: (num_boxes, 4)
        
        # Add detected boxes to SAM 2 for segmentation
        for single_box in detected_boxes:
            # SAM expects boxes in [x1, y1, x2, y2] format
            try:
                _, out_obj_ids, out_mask_logits = predictor.add_new_points_or_box(
                    inference_state=inference_state,
                    frame_idx=int(frame_idx),
                    obj_id=ann_obj_id,
                    box=single_box.tolist(),  # Convert to list if necessary
                )
                ann_obj_id += 1
            except Exception as e:
                print(f"Error processing frame {frame_idx} with box {single_box}: {e}")
                continue
    
        # Propagate masks in video after adding new objects
        try:
            video_segments[int(frame_idx)] = {
                out_obj_id: (out_mask_logits[i] > 0.0).cpu().numpy()
                for i, out_obj_id in enumerate(out_obj_ids)
            }
        except Exception as e:
            print(f"Error propagating masks for frame {frame_idx}: {e}")
            continue
    
    # Clear cache to free up memory
    torch.cuda.empty_cache()

# Save the Segmented Video
def save_segmented_video(output_path, frame_names, video_segments, target_size=(320, 320)):
    height, width = target_size
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = cv2.VideoWriter(output_path, fourcc, fps, (width, height))
    
    for idx in tqdm(range(len(frame_names)), desc="Saving video"):
        frame_path = os.path.join(output_frames_dir, frame_names[idx])
        frame = cv2.imread(frame_path)
        if frame is None:
            print(f"Warning: Unable to read frame at {frame_path}. Skipping.")
            continue
        frame = cv2.resize(frame, (width, height))  # Ensure size matches target_size

        if idx in video_segments:
            for out_obj_id, out_mask in video_segments[idx].items():
                # Squeeze the mask to remove any single-dimensional entries
                out_mask = np.squeeze(out_mask)

                # Debug: Print the mask shape after squeezing
                print(f"Debug: Frame {idx} - Mask shape after squeezing: {out_mask.shape}")
                print(f"Debug: Frame {idx} - Mask values min: {out_mask.min()}, max: {out_mask.max()}")

                # Convert mask to uint8 and ensure it's single-channel
                mask = (out_mask * 255).astype(np.uint8)
                
                # Check if resizing parameters are valid and the mask is non-empty
                if mask.shape[0] > 0 and mask.shape[1] > 0 and width > 0 and height > 0:
                    mask = cv2.resize(mask, (width, height))  # Resize mask to match frame size
                else:
                    print(f"Error: Invalid mask size or target size for resizing mask in frame {idx}. Skipping.")
                    continue

                # Define the color for the mask (Green in this case)
                color = np.array([0, 255, 0], dtype=np.uint8)  # BGR format for OpenCV

                # Create a 3-channel colored mask
                colored_mask = np.zeros_like(frame, dtype=np.uint8)
                for c in range(3):
                    colored_mask[:, :, c] = mask  # Apply mask to all three channels

                # Apply the colored mask on the frame
                blended_frame = cv2.addWeighted(frame, 1.0, colored_mask, 0.5, 0)
                
                # Debug: Save or display the frame with applied mask to check results
                debug_frame_path = os.path.join(output_frames_dir, f"debug_{idx:05d}.jpg")
                cv2.imwrite(debug_frame_path, blended_frame)

                frame = blended_frame
        
        out.write(frame)
    
    out.release()
    print(f'Segmented video saved to {output_path}')


save_segmented_video(output_video_path, frame_names, video_segments, target_size=(320, 320))


Extracting frames: 100%|██████████| 153/153 [00:06<00:00, 23.43it/s]


Using device: cuda


Processing batches:   0%|          | 0/153 [00:00<?, ?it/s]


0: 320x320 2 cars, 7.6ms
Speed: 0.0ms preprocess, 7.6ms inference, 1.0ms postprocess per image at shape (1, 3, 320, 320)


Processing batches:   1%|          | 1/153 [00:02<05:24,  2.13s/it]

...

Debug: Frame 150 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 150 - Mask values min: False, max: True
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask value

Saving video:  99%|█████████▉| 152/153 [07:27<00:05,  5.53s/it]

Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask values min: False, max: False
Debug: Frame 151 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 151 - Mask valu

Saving video: 100%|██████████| 153/153 [07:32<00:00,  2.95s/it]

Debug: Frame 152 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 152 - Mask values min: False, max: False
Debug: Frame 152 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 152 - Mask values min: False, max: False
Debug: Frame 152 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 152 - Mask values min: False, max: False
Debug: Frame 152 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 152 - Mask values min: False, max: False
Debug: Frame 152 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 152 - Mask values min: False, max: False
Debug: Frame 152 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 152 - Mask values min: False, max: False
Debug: Frame 152 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 152 - Mask values min: False, max: False
Debug: Frame 152 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 152 - Mask values min: False, max: False
Debug: Frame 152 - Mask shape after squeezing: (1080, 2520)
Debug: Frame 152 - Mask valu